In [1]:
!pip install transformers

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 4.4 MB 9.8 MB/s 
     |████████████████████████████████| 101 kB 12.3 MB/s 
     |████████████████████████████████| 6.6 MB 48.5 MB/s 
     |████████████████████████████████| 596 kB 54.1 MB/s 
  Attempting uninstall: pyyaml
    Found existing installation: PyYAML 3.13
    Uninstalling PyYAML-3.13:
      Successfully uninstalled PyYAML-3.13


In [2]:
!pip install bertviz

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 157 kB 7.5 MB/s 
     |████████████████████████████████| 132 kB 48.1 MB/s 
     |████████████████████████████████| 1.2 MB 38.5 MB/s 
     |████████████████████████████████| 9.0 MB 30.9 MB/s 
     |████████████████████████████████| 79 kB 6.0 MB/s 
     |████████████████████████████████| 139 kB 47.6 MB/s 
     |████████████████████████████████| 127 kB 40.2 MB/s 
  Attempting uninstall: urllib3
    Found existing installation: urllib3 1.24.3
    Uninstalling urllib3-1.24.3:
      Successfully uninstalled urllib3-1.24.3
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
datascience 0.10.6 requires folium==0.2.1, but you have folium 0.8.3 which is incompatible.


In [3]:
from transformers import AutoTokenizer
from bertviz.transformers_neuron_view import BertModel
from bertviz.neuron_view import show

In [4]:
model_ckpt = "bert-base-uncased"
tokenizer = AutoTokenizer.from_pretrained(model_ckpt)
model = BertModel.from_pretrained(model_ckpt)

Downloading:   0%|          | 0.00/28.0 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/570 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/226k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/455k [00:00<?, ?B/s]

100%|██████████| 440473133/440473133 [00:15<00:00, 27860419.62B/s]


In [6]:
text = "Movement is the engine of life."

In [7]:
show(model, "bert", tokenizer, text, display_mode="light", layer=0, head=8)

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

**Attention nitty-gritty. Implementation**


In [8]:
import torch
import torch.nn.functional as F
from bertviz import head_view
from math import sqrt
from torch import nn
from transformers import AutoConfig, AutoModel

In [9]:
inputs = tokenizer(text, return_tensors="pt", add_special_tokens=False)
inputs.input_ids


tensor([[2929, 2003, 1996, 3194, 1997, 2166, 1012]])

In [10]:
config = AutoConfig.from_pretrained(model_ckpt)
token_emb = nn.Embedding(config.vocab_size, config.hidden_size)
token_emb

Embedding(30522, 768)

In [11]:
inputs_embeds = token_emb(inputs.input_ids)
inputs_embeds.size()

torch.Size([1, 7, 768])

In [13]:
inputs_embeds

tensor([[[ 0.3091,  0.9690, -1.5161,  ..., -1.0187,  0.6506, -1.0578],
         [ 0.1986, -0.2202, -0.9473,  ...,  0.7120, -0.7201,  0.0472],
         [ 1.2423, -0.4542, -0.0624,  ...,  1.5628, -0.5497, -0.1707],
         ...,
         [ 1.5581, -2.8438,  0.4549,  ...,  1.3680,  0.3433,  0.4554],
         [ 0.7591, -0.9995, -0.2626,  ...,  0.1175,  1.8920,  0.6680],
         [ 1.1718,  0.2876, -1.1985,  ..., -1.3993,  0.4017,  0.7539]]],
       grad_fn=<EmbeddingBackward0>)

In [14]:
query = key = value = inputs_embeds
dim_k = key.size(-1)

# bmm - matrix multiplication in batches 
scores = torch.bmm(query, key.transpose(1,2)) / sqrt(dim_k)
scores.size()

torch.Size([1, 7, 7])

Apply softmax:

In [16]:
weights = F.softmax(scores, dim=-1)
weights.sum(dim=-1)

tensor([[1., 1., 1., 1., 1., 1., 1.]], grad_fn=<SumBackward1>)

Multiply attention weights by the values:

In [17]:
attn_outputs = torch.bmm(weights, value) # batch matrix multiplication
attn_outputs.shape

torch.Size([1, 7, 768])

In [18]:
def scaled_dot_product_attention(query, key, value, mask=None):
  dim_k = key.size(-1)
  scores = torch.bmm(query, key.transpose(1,2)) / sqrt(dim_k)
  if mask is not None:
    scores = scores.masked_fill(mask==0, float("-inf"))
  weights = F.softmax(scores, dim=-1)
  return torch.bmm(weights, value)

In [19]:
class AttentionHead(nn.Module):
    def __init__(self, embed_dim, head_dim):
        super().__init__()
        self.q = nn.Linear(embed_dim, head_dim)
        self.k = nn.Linear(embed_dim, head_dim)
        self.v = nn.Linear(embed_dim, head_dim)
    
    def forward(self, hidden_state):
        return scaled_dot_product_attention(self.q(hidden_state),
                                                    self.k(hidden_state),
                                                    self.v(hidden_state))
      

In [20]:
class MultiHeadAttention(nn.Module):
    def __init__(self, config):
        super().__init__()
        embed_dim = config.hidden_size
        num_heads = config.num_attention_heads
        head_dim = embed_dim // num_heads
        self.heads = nn.ModuleList([AttentionHead(embed_dim, head_dim) for x in range(num_heads)])
        self.output_linear = nn.Linear(embed_dim, embed_dim)

    def forward(self, hidden_state):
        r = torch.cat([h(hidden_state) for h in self.heads], dim=-1)
        r = self.output_linear(r)
        return r

In [21]:
multihead_attn = MultiHeadAttention(config)
attn_output = multihead_attn(inputs_embeds)
attn_output.size()

torch.Size([1, 7, 768])

In [22]:
model = AutoModel.from_pretrained(model_ckpt, output_attentions=True)
seq_a = text
seq_b = "Car engine is its heart."

Downloading:   0%|          | 0.00/420M [00:00<?, ?B/s]

Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertModel: ['cls.predictions.transform.dense.bias', 'cls.predictions.bias', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.dense.weight', 'cls.seq_relationship.weight', 'cls.predictions.decoder.weight', 'cls.seq_relationship.bias']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


In [23]:
viz_inputs = tokenizer(seq_a, seq_b, return_tensors="pt")
attn = model(**viz_inputs).attentions
seq_b_start = (viz_inputs.token_type_ids==0).sum(dim=1)
tokens = tokenizer.convert_ids_to_tokens(viz_inputs.input_ids[0])

head_view(attn, tokens, seq_b_start, heads=[8])

<IPython.core.display.Javascript object>